In [3]:
%config Completer.use_jedi = False
from datetime import datetime
import pandas as pd
import numpy as np
import json
import folium
from folium import GeoJson

In [4]:
###################################
# loading crime data
###################################
carpetas = pd.read_csv('./carpetas_investigacion/carpetas_completa_abril_2021.csv')
carpetas_latlong=carpetas.drop(carpetas.loc[carpetas.latitud.isna()].index)
columns = ['fecha_hechos',
           'fecha_inicio',
           'delito',
           'categoria_delito',
           'longitud',
           'latitud',]
delitos = carpetas_latlong[columns].copy()
delitos['fecha_hechos'] = np.where(
                            delitos['fecha_hechos']==np.nan, 
                            delitos['fecha_inicio'], 
                            delitos['fecha_hechos'])
delitos['fecha_hechos']=pd.to_datetime(delitos.fecha_hechos).dt.date
delitos['fecha_inicio']=pd.to_datetime(delitos.fecha_inicio).dt.date
inicio = datetime.strptime('2000-01-01', '%Y-%m-%d').date()
delitos_milenio = delitos[delitos.fecha_hechos>=inicio].copy()


20787      2000-01-01
848093     2000-01-01
221463     2000-01-01
971526     2000-01-02
980293     2000-01-05
              ...    
1208196    2021-04-30
1207723    2021-04-30
1207888    2021-04-30
1208164    2021-04-30
1207822    2021-04-30
Name: fecha_hechos, Length: 1159322, dtype: object

In [ ]:
###################################
# loading census data
###################################
censo_cdmx = pd.read_csv('censo20_cdmx_por_ageb/conjunto_de_datos_ageb_urbana_09_cpv2020.csv')

# censo_cdmx.shape
numeric_cols = censo_cdmx.select_dtypes(include=np.number).columns.tolist()
for e in numeric_cols[0:-2]:
    censo_cdmx[e] = censo_cdmx[e].apply(str)

totales_agebs = censo_cdmx[(censo_cdmx.MZA=='0')].copy()
totales_ent_mun = totales_agebs[totales_agebs.AGEB == '0000'].copy()
totales_agebs = totales_agebs.drop(totales_agebs.loc[(totales_agebs.AGEB == '0000')].index)

In [ ]:
columns = ['ENTIDAD',
           'MUN',
           'LOC',
           'AGEB',
           'POBTOT',
           'POBFEM',
           'POBMAS',
           'GRAPROES', 
           'GRAPROES_F', 
           'GRAPROES_M', 
           'POCUPADA', 
           'POCUPADA_F', 
           'POCUPADA_M', 
           'PDESOCUP', 
           'PDESOCUP_F',
           'PDESOCUP_M', 
           'VIVPAR_HAB', 
           'PRO_OCUP_C']

In [ ]:
my_data = totales_agebs[columns].copy()
my_data.head()

In [27]:
###################################
# loading basic geostatistical area (AGEB)
###################################
location=[19.436677, -99.143422]
zoom_start=11

with open('ageb_cdmx_epsg4326.geojson') as f:
    agebs = json.load(f)


In [38]:
agebs.keys()

dict_keys(['type', 'name', 'crs', 'features'])

In [46]:
agebs['features'][0]

{'type': 'Feature',
 'properties': {'CVE_ENT': '09',
  'CVE_MUN': '003',
  'CVE_LOC': '0001',
  'CVE_AGEB': '1783'},
 'geometry': {'type': 'MultiPolygon',
  'coordinates': [[[[-99.17286695004587, 19.30630287960931],
     [-99.17283746017237, 19.306249319708616],
     [-99.17209895499188, 19.3049186143727],
     [-99.17293592877996, 19.304500926019504],
     [-99.1738865303828, 19.304026564774592],
     [-99.173871464768, 19.30399360514379],
     [-99.17383049655629, 19.3039039166492],
     [-99.17523896987458, 19.303289614951098],
     [-99.17526014970962, 19.303268399896893],
     [-99.17526332807553, 19.30324463830861],
     [-99.17527239460661, 19.303176849395687],
     [-99.17528785019563, 19.303061219900155],
     [-99.17588819986265, 19.303147570116955],
     [-99.17654937987665, 19.30323111015608],
     [-99.17679900000849, 19.303272820271115],
     [-99.17711555030519, 19.3033134904187],
     [-99.1771325915772, 19.30331563280461],
     [-99.17732398032106, 19.303331550172626],

In [30]:
# simple map load
m = folium.Map(location=location, zoom_start=zoom_start)
#folium.GeoJson(agebs,).add_to(m)




In [31]:
folium.GeoJson(
    agebs,
    style_function=lambda feature: {
        "fillColor": "#ffff00",
        "color": "black",
        "weight": 2,
        "dashArray": "5, 5",
    },
).add_to(m)

In [32]:
m
